In [28]:
!pip install azure-storage-blob
import os
import requests
import json
import time
from tqdm import tqdm
from azure.storage.blob import BlobServiceClient, BlobClient, ContainerClient
import re

# Configuration
SEARCH_QUERY = "your search query"
API_URL = "https://commons.wikimedia.org/w/api.php"
RESULTS_PER_REQUEST = 500  # Max value allowed by Wikimedia API
USER_AGENT = "your email"  # Modify with your email or app name

# Azure Blob Storage Configuration
connection_string = "your azure connection string"
container_name = "your blob container name"

# Create the BlobServiceClient
blob_service_client = BlobServiceClient.from_connection_string(connection_string)

def sanitize_blob_name(blob_name, is_json=False):
    """Sanitize blob name and enforce proper extension."""
    # Remove 'File:' prefix if present
    blob_name = blob_name.replace('File:', '').strip()

    # Replace spaces with underscores
    blob_name = blob_name.replace(' ', '_')

    # Remove all characters that are not alphanumeric, '-', or '_'
    blob_name = re.sub(r'[^a-zA-Z0-9_-]', '', blob_name)

    # Ensure the name doesn't start or end with invalid characters
    blob_name = blob_name.strip("_")

    if is_json:
        # For JSON files, ensure .json extension
        if not blob_name.lower().endswith('.json'):
            blob_name += '.json'
    else:
        # For images, handle extensions
        img_extensions = {'.jpg', '.jpeg', '.png', '.gif', '.webp'}
        lower_name = blob_name.lower()

        if not any(lower_name.endswith(ext) for ext in img_extensions):
            blob_name += '.jpg'
        elif lower_name.endswith('.jpeg'):
            blob_name = blob_name[:-5] + '.jpg'
        elif blob_name.endswith('.JPG'):
            blob_name = blob_name[:-4] + '.jpg'

    return blob_name

def upload_to_blob(data, filename, is_json=False):
    """Uploads data to Azure Blob Storage with sanitized blob name."""
    sanitized_filename = sanitize_blob_name(filename, is_json)
    blob_client = blob_service_client.get_blob_client(container=container_name, blob=sanitized_filename)

    try:
        blob_client.upload_blob(data, overwrite=True)
        print(f"Successfully uploaded {sanitized_filename} to Blob Storage.")
        return True
    except Exception as e:
        print(f"Error uploading {sanitized_filename} to Blob Storage: {e}")
        return False

def fetch_image_metadata():
    """Fetch metadata with progress tracking and handle pagination."""
    params = {
        'action': 'query',
        'format': 'json',
        'generator': 'search',
        'gsrsearch': SEARCH_QUERY,
        'gsrnamespace': '6',
        'gsrlimit': RESULTS_PER_REQUEST,
        'prop': 'imageinfo',
        'iiprop': 'url|extmetadata',
        'iiextmetadatafilter': 'ObjectName|DateTimeOriginal|ImageDescription|Medium|Culture'
    }

    headers = {'User-Agent': USER_AGENT}
    images = []

    with tqdm(desc="Fetching images metadata") as pbar:
        while True:
            response = requests.get(API_URL, params=params, headers=headers)
            data = response.json()

            if 'query' in data:
                images.extend(data['query']['pages'].values())
                pbar.update(len(data['query']['pages']))

            if 'continue' in data:
                params.update(data['continue'])
                time.sleep(1)
            else:
                break

    return images

def process_images(images):
    """Download images and metadata, then upload to Blob Storage."""
    MAX_RETRIES = 3

    for img in tqdm(images, desc="Processing images"):
        filename_base = img['title'].replace('File:', '').replace('/', '_')
        image_url = img['imageinfo'][0]['url']
        metadata = img['imageinfo'][0]['extmetadata']

        # Prepare metadata
        clean_metadata = {
            "ObjectName": metadata.get('ObjectName', {}).get('value', ''),
            "ImageDescription": metadata.get('ImageDescription', {}).get('value', ''),
            "Medium": metadata.get('Medium', {}).get('value', ''),
            "Culture": metadata.get('Culture', {}).get('value', '')
        }

        # Convert metadata to JSON bytes
        json_data = json.dumps(clean_metadata, indent=2, ensure_ascii=False).encode('utf-8')

        # Upload metadata first
        json_filename = f"{filename_base}_metadata"
        upload_to_blob(json_data, json_filename, is_json=True)

        # Then upload image
        attempt = 0
        while attempt < MAX_RETRIES:
            try:
                response = requests.get(image_url, headers={'User-Agent': USER_AGENT}, stream=True, timeout=30)
                response.raise_for_status()
                upload_to_blob(response.content, filename_base)
                break
            except requests.exceptions.RequestException as e:
                print(f"Error downloading {filename_base}: {e}")
                attempt += 1
                if attempt == MAX_RETRIES:
                    print(f"Failed to download {filename_base} after {MAX_RETRIES} attempts")
                else:
                    time.sleep(2 ** attempt)

# Main execution
print(f"🔍 Searching for '{SEARCH_QUERY}'...")
images = fetch_image_metadata()

if images:
    print(f"\nFound {len(images)} images.")
    confirm = input("Proceed with download and upload to Blob Storage? (y/n): ")

    if confirm.lower() == 'y':
        print(f"⏳ Downloading and uploading {len(images)} images and metadata to Blob Storage...")
        process_images(images)
        print(f"\n✅ Done! Files uploaded to Azure Blob Storage.")
    else:
        print("🚫 Operation cancelled")
else:
    print("❌ No images found.")

🔍 Searching for 'bronze bust'...


Fetching images metadata: 10000it [04:37, 36.08it/s]



Found 10000 images.
Proceed with download and upload to Blob Storage? (y/n): y
⏳ Downloading and uploading 10000 images and metadata to Blob Storage...


Processing images:   0%|          | 0/10000 [00:00<?, ?it/s]

Successfully uploaded Saint_Paschal_Baylon_Reliquary_bust_1845_by_Vincenzo_Caruso_-_Embossed_and_cast_silver_gilt_bronze_-_Treasure_of_Saint_January_in_Naples_Cathedraljpg_metadata.json to Blob Storage.


...

Successfully uploaded Works_IA_worksstevenson03stevialapdf.jpg to Blob Storage.
Successfully uploaded Works_of_art_from_the_Byzantine_period_to_that_of_Louis_Seize_IA_artbyzantineper00chripdf_metadata.json to Blob Storage.


Processing images: 100%|█████████▉| 9999/10000 [3:01:54<00:03,  3.47s/it]

Successfully uploaded Works_of_art_from_the_Byzantine_period_to_that_of_Louis_Seize_IA_artbyzantineper00chripdf.jpg to Blob Storage.
Successfully uploaded tude_sur_la_mlancolie_IA_b22268340pdf_metadata.json to Blob Storage.


Processing images: 100%|██████████| 10000/10000 [3:01:55<00:00,  1.09s/it]

Successfully uploaded tude_sur_la_mlancolie_IA_b22268340pdf.jpg to Blob Storage.

✅ Done! Files uploaded to Azure Blob Storage.
